# Наивный Байес и спам
__Суммарное количество баллов: 10__


In [3]:
from sklearn.model_selection import train_test_split
import numpy as np
import pandas
import random
import matplotlib.pyplot as plt
import matplotlib
import copy
import spacy
from nltk.stem.snowball import SnowballStemmer

In [4]:
import re
def read_dataset(filename):
    file = open(filename, encoding="utf-8")
    x = []
    y = []
    for line in file:
        cl, sms = re.split("^(ham|spam)[\t\s]+(.*)$", line)[1:3]
        x.append(sms)
        y.append(cl)
    return np.array(x, dtype=np.str), np.array(y, dtype=np.str)

In [5]:
def get_precision_recall_accuracy(y_pred, y_true):
    classes = np.unique(list(y_pred) + list(y_true))
    true_positive = dict((c, 0) for c in classes)
    true_negative = dict((c, 0) for c in classes)
    false_positive = dict((c, 0) for c in classes)
    false_negative = dict((c, 0) for c in classes)
    for c_pred, c_true in zip(y_pred, y_true):
        for c in classes:
            if c_true == c:
                if c_pred == c_true:
                    true_positive[c] = true_positive.get(c, 0) + 1
                else:
                    false_negative[c] = false_negative.get(c, 0) + 1
            else:
                if c_pred == c:
                    false_positive[c] = false_positive.get(c, 0) + 1
                else:
                    true_negative[c] = true_negative.get(c, 0) + 1
    precision = dict((c, true_positive[c] / (true_positive[c] + false_positive[c])) for c in classes)
    recall = dict((c, true_positive[c] / (true_positive[c] + false_negative[c])) for c in classes)
    accuracy = sum([true_positive[c] for c in classes]) / len(y_pred)
    return precision, recall, accuracy

def plot_precision_recall(X_train, y_train, X_test, y_test, bow_method, voc_sizes=range(4, 200, 5)):
    classes = np.unique(list(y_train) + list(y_test))
    precisions = dict([(c, []) for c in classes])
    recalls = dict([(c, []) for c in classes])
    accuracies = []
    for v in voc_sizes:
        bow = bow_method(X_train, voc_limit=v)
        X_train_transformed = bow.transform(X_train)
        X_test_transformed = bow.transform(X_test)
        classifier = NaiveBayes(0.001)
        classifier.fit(X_train_transformed, y_train)
        y_pred = classifier.predict(X_test_transformed)
        precision, recall, acc = get_precision_recall_accuracy(y_pred, y_test)
        for c in classes:
            precisions[c].append(precision[c])
            recalls[c].append(recall[c])
        accuracies.append(acc)
    def plot(x, ys, ylabel, legend=True):        
        plt.figure(figsize = (12, 3))
        plt.xlabel("Vocabulary size")
        plt.ylabel(ylabel)
        plt.xlim(x[0], x[-1])
        plt.ylim(np.min(list(ys.values()))-0.01, np.max(list(ys.values()))+0.01)
        for c in ys.keys():
            plt.plot(x, ys[c], label="Class " + str(c))
        if legend:
            plt.legend()
        plt.tight_layout()
        plt.show()
    
    plot(voc_sizes, recalls, "Recall")
    plot(voc_sizes, precisions, "Precision")
    plot(voc_sizes, {"":accuracies}, "Accuracy", legend=False)

In [6]:
X, y = read_dataset("spam")

In [7]:
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.9)

In [95]:
y_test

array(['ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'spam',
       'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'spam', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham',
       'spam', 'spam', 'ham', 'ham', 'spam', 'spam', 'ham', 'spam', 'ham',
       'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham', 'ham',
       'ham', 'ham', 'ham', 'spam', 'ham', 'ham', 'ham', 'ham', 'ham',
       'spam', 'ham', 'ham', 'ham', 'ham', 'ham', 'spam', 'ham', 'ham',
    

### Задание 1 (3 балла)
Реализуйте классификацию методом Байеса в предположении независимости компонент `x`. При реализации следует считать, что значения каждой компоненты дискретны, а `p(x|y)` имеет мультиномиальное распределение.

#### Методы
`fit(X, y)` - оценивает параметры распределения `p(x|y)` для каждого `y`. 

`log_proba(X)` - для каждого элемента набора `X` считает логарифм вероятности отнести его к каждому классу. По теореме Байеса: `p(y|x) = p(y)p(x|y)/p(x)`. Соответственно, после логарифмирования: `log p(y|x) = log p(y) + log p(x|y) - log p(x)`. Поскольку `log p(x)` является независящей от класса `y` константой, это слагаемое никак не влияет на решение задачи максимизации. Поэтому его можно просто убрать для простоты.

In [131]:
import math

In [172]:
class NaiveBayes:
    alpha = None
    freq = None
    label_count = None
    classes = None
    def __init__(self, alpha):
        self.alpha = alpha # Параметр аддитивной регуляризации
    
    def fit(self, X, y):
        labels = list(np.unique(y))
        self.classes = labels
        self.freq = [[[0 for _ in range(2)] for _ in range(len(labels))] for _ in range(len(X[0]))]
        label_count = [0 for _ in range(len(labels))]
        n = len(X)
        for i in range(n):
            features = X[i]
            label = labels.index(y[i]) # Найти номер лейбла
            label_count[label] += 1
            for j in range(len(features)):
                feat = features[j]
                self.freq[j][label][feat]+=1
        print(label_count)
        for i in range(len(self.freq)):
            for j in range(len(labels)):
                for k in range(len(self.freq[i][j])):
                    print(self.freq[i][j][k])
                    self.freq[i][j][k] = (self.freq[i][j][k]+self.alpha)/(label_count[j] + len(X[0])*self.alpha)
                print(bow.res[i])
                print(self.freq[i][j])
        for i in range(len(labels)):
            label_count[i] /= len(X)
        self.label_count = label_count
        
    def predict(self, X):
#         print([self.classes[i] for i in np.argmax(self.log_proba(X), axis=1)])
        return [self.classes[i] for i in np.argmax(self.log_proba(X), axis=1)]
    
    def log_proba(self, X):
        result = []
        for i in range(len(X)): # Для каждого предложения
            x = X[i]
            if y_test[i] == "spam":
                print(x)
            res1 = []
            p=0
            for label in range(len(self.label_count)):
                for feat in range(len(x)):
                    p+=math.log(self.freq[feat][label][x[feat]]) # Все вероятности для лейбла
                    if y_test[i] == "spam":
                        print(math.log(self.freq[feat][label][x[feat]]))
                if y_test[i] == "spam":
                    print(p, math.log(self.label_count[label]))
                p+=math.log(self.label_count[label])
                res1.append(p)
#             if res1[0] < res1[1]:
#                 print(res1)
            if y_test[i] == "spam":
                print(res1)
            result.append(res1)
        return result

### Задание 2 (3 балла)
Теперь реализуем метод bag of words. Задача состоит в том, чтобы посчитать количество вхождений каждого слова в предложение.

#### Методы
`__init__(X, voc_limit)` - инициализирует BoW, составляя словарь, который будет использоваться для векторизации предложений. Размер словаря должен быть не больше `voc_limit`, в него должны входить самые часто встречающиеся в выборке слова.

`transform(X)` - векторизует сообщения из набора.

In [133]:
from collections import defaultdict

In [127]:
class BoW:
    res = None
    def __init__(self, X, voc_limit=1000):
        tmp = defaultdict(int)
        for st in X:
            for word in st.split():
                word = ''.join(x.lower() for x in word if x.isalpha()) # Очищаем слово
                if word != "":
                    tmp[word]+=1
        self.res = sorted(tmp.items(), key=lambda kv: kv[1], reverse = True)[:voc_limit] # Нашли самые частые слова
        self.res = list(map(lambda x: x[0], self.res))
#         print(self.res)
        
    def transform(self, X):
        result = []
        for st in X:
            res1 = []
            tmp = defaultdict(int)
            for word in st.split():
                word = ''.join(x.lower() for x in word if x.isalpha())
                if word != "":
                    tmp[word]+=1 # Считаем количество слов
            for el in self.res:
                if tmp[el] != 0:
                    res1.append(1) # Записываем в вектор 1, если слово встретилось
                else:
                    res1.append(0)
            result.append(res1)
        return result

In [164]:
bow = BoW(X_train, voc_limit=500)
X_train_bow = bow.transform(X_train)
X_test_bow = bow.transform(X_test)

In [173]:
predictor = NaiveBayes(0.001)
predictor.fit(X_train_bow, y_train)
print(list(zip(predictor.predict(X_test_bow), y_test)))
get_precision_recall_accuracy(predictor.predict(X_test_bow), y_test)

[4343, 673]
3245
1098
to
[0.7470935881201797, 0.25279175779901003]
251
422
to
[0.3726815144766147, 0.6265790645879732]
2934
1409
i
[0.6754923448831588, 0.32439300103603086]
635
38
i
[0.942837416481069, 0.05642316258351893]
3185
1158
you
[0.733279843444227, 0.26660550247496256]
462
211
you
[0.6859703043801039, 0.31329027468448406]
3558
785
a
[0.8191552895130656, 0.18073005640612408]
405
268
a
[0.6013377876763177, 0.3979227913882702]
3563
780
the
[0.8203064349027283, 0.17957891101646137]
527
146
the
[0.7824810690423162, 0.21677951002227172]
3711
632
u
[0.8543803384367447, 0.14550500748244502]
562
111
u
[0.8344484038604305, 0.1648121752041574]
3727
616
and
[0.8580640036836653, 0.14182134223552434]
577
96
and
[0.8567201187824796, 0.1425404602821084]
3788
555
is
[0.8721079774375504, 0.12777736848163923]
544
129
is
[0.8077223459539717, 0.19153823311061619]
3689
654
in
[0.8493152987222287, 0.15057004719696096]
616
57
in
[0.9146265775798069, 0.084634001484781]
3750
593
me
[0.8633592724761138, 

673
0
having
[0.9992590942835932, 1.4847809948032666e-06]
4308
35
dat
[0.9918270979624727, 0.008058247956716932]
673
0
dat
[0.9992590942835932, 1.4847809948032666e-06]
4340
3
latest
[0.9991944284563141, 0.0006909174628755611]
641
32
latest
[0.9517461024498886, 0.047514476614699326]
4333
10
holiday
[0.9975828249107863, 0.0023025210084033614]
646
27
holiday
[0.9591700074239049, 0.040090571640683]
4307
36
few
[0.9915968688845401, 0.008288477034649475]
673
0
few
[0.9992590942835932, 1.4847809948032666e-06]
4307
36
yup
[0.9915968688845401, 0.008288477034649475]
673
0
yup
[0.9992590942835932, 1.4847809948032666e-06]
4308
35
finish
[0.9918270979624727, 0.008058247956716932]
673
0
finish
[0.9992590942835932, 1.4847809948032666e-06]
4340
3
receive
[0.9991944284563141, 0.0006909174628755611]
645
28
receive
[0.9576852264291017, 0.04157535263548627]
4320
23
end
[0.9945898468976633, 0.005295499021526419]
664
9
end
[0.9858960653303638, 0.0133645137342242]
4308
35
car
[0.9918270979624727, 0.008058247

-0.0065829184327633765
-0.006351195625961857
-0.004730637711528083
-0.0065829184327633765
-0.0017279799532133196
-0.005887911036550851
-0.004499343673557989
-0.00011489090959606616
-0.005656349204223256
-0.0065829184327633765
-0.0017279799532133196
-0.006119526502180301
-0.000575508038740357
-0.0038057823681145824
-0.005887911036550851
-0.005656349204223256
-0.004036916026572435
-0.006351195625961857
-0.0003451729531509884
-0.002650914738862028
-0.005656349204223256
-0.005887911036550851
-0.0012668317922046551
-0.006351195625961857
-0.005887911036550851
-0.004961985258806911
-0.005656349204223256
-0.0054248409803644175
-0.0054248409803644175
-0.005887911036550851
-0.005887911036550851
-0.0017279799532133196
-0.006119526502180301
-0.006119526502180301
-0.0051933863401585866
-0.00011489090959606616
-0.005887911036550851
-0.004961985258806911
-0.005887911036550851
-0.006119526502180301
-0.0028817815918171044
-0.005656349204223256
-0.0010363374338012697
-0.004961985258806911
-0.00588791103

-0.005656349204223256
-0.0054248409803644175
-0.005656349204223256
-0.0054248409803644175
-0.0017279799532133196
-0.004036916026572435
-0.004499343673557989
-0.00311270175658403
-5.331865698062684
-0.0054248409803644175
-0.0051933863401585866
-0.0051933863401585866
-0.00011489090959606616
-0.004730637711528083
-0.0008058961908045737
-0.0038057823681145824
-0.004961985258806911
-0.0051933863401585866
-0.004730637711528083
-0.00011489090959606616
-0.00011489090959606616
-0.00011489090959606616
-0.0012668317922046551
-0.0028817815918171044
-0.004268103120149363
-0.004961985258806911
-0.0051933863401585866
-0.004036916026572435
-0.00011489090959606616
-0.004961985258806911
-0.004499343673557989
-0.0051933863401585866
-0.004499343673557989
-80.250463600546 -0.1440674497779348
-0.46748031214896824
-0.05886142215581747
-0.376920940268858
-0.9214972840032399
-0.24528554977764994
-1.8029487855696564
-0.15464399624156794
-0.21353691076087153
-0.08923940894159325
-3.3343924997038377
-0.0126994514

-0.008438636465719756
-0.007278409200222754
-0.008670843541601777
-0.008206483297446224
-0.0008058961908045737
-0.0024201011731087327
-0.008438636465719756
-0.008438636465719756
-0.008206483297446224
-0.0008058961908045737
-0.0054248409803644175
-0.008206483297446224
-0.006814694947469674
-0.007510346988126101
-0.007046525194982873
-0.00011489090959606616
-0.0008058961908045737
-0.0024201011731087327
-0.005656349204223256
-0.006814694947469674
-0.007278409200222754
-0.0065829184327633765
-0.005887911036550851
-0.004499343673557989
-0.005656349204223256
-0.007278409200222754
-0.007742338583647168
-0.005887911036550851
-0.0051933863401585866
-0.007974384011757464
-0.007046525194982873
-0.005656349204223256
-5.811409476119944
-0.007742338583647168
-0.007742338583647168
-0.006351195625961857
-0.007278409200222754
-0.007046525194982873
-0.0065829184327633765
-0.007510346988126101
-0.005656349204223256
-0.007278409200222754
-0.006351195625961857
-0.006814694947469674
-0.005656349204223256
-0

...

-0.04292480439021827
-0.025533065821914336
-0.03717353182780199
-0.03765154319493175
-0.0359795021203357
-0.03335764449205924
-0.03335764449205924
-0.025533065821914336
-4.3333669421596674
-0.025533065821914336
-0.02813446196757513
-0.03550228914950721
-0.03264378383446518
-0.02813446196757513
-0.030742643029233165
-0.03169276163987211
-6.073750665705596
-0.030980088064791272
-0.03335764449205924
-0.025296910486339468
-0.031217589493885037
-0.02624186662919107
-0.026714679764993872
-0.02506081090694015
-0.027897691571481507
-0.03026792203164492
-0.012626636028540349
-4.850045817751625
-0.027187716558810564
-0.0033436752577902596
-0.008903104550133786
-0.014727231479300194
-0.024116969624942922
-0.02011555296463875
-0.02624186662919107
-0.027424318893617818
-0.02624186662919107
-0.024352846442671383
-0.01800362025707998
-0.02199657823569733
-0.024824767057394687
-0.019880673394534712
-0.015194630303560826
-0.023409672815377834
-0.020820522866947685
-0.016130083848050456
-0.0189417064098

-0.01571149737006774
-0.030909335181592123
-0.026325682517247654
-0.01571149737006774
-1.4690564273390803
-0.04634171640405527
-0.008198325308905461
-0.1721269284557916
-0.08115530361227836
-0.0007411803226937619
-0.027851233498775028
-0.037053738315466496
-0.023281544769417455
-0.011196823809655296
-0.02024664567958021
-0.0007411803226937619
-0.0037173685668816657
-0.00969645068554409
-0.008198325308905461
-0.014204340351022483
-0.01571149737006774
-0.01722092934053334
-0.12224565093412752
-0.02480245529695128
-0.02480245529695128
-0.01571149737006774
-0.00969645068554409
-0.037053738315466496
-0.0908641020289626
-1.9798777500668003
-0.044787716952239646
-0.0007411803226937619
-0.006702440954996565
-0.00969645068554409
-0.04168694408139893
-0.011196823809655296
-0.014204340351022483
-1.6372830390906166
-0.0007411803226937619
-0.0022281672331383034
-0.032441900182610624
-0.0022281672331383034
-0.0007411803226937619
-0.030909335181592123
-0.014204340351022483
-0.027851233498775028
-0.01

-0.0007411803226937619
-0.0007411803226937619
-0.01269945143629674
-0.0037173685668816657
-0.0007411803226937619
-0.008198325308905461
-0.0007411803226937619
-0.006702440954996565
-0.0022281672331383034
-0.030909335181592123
-0.035514094500380844
-0.00969645068554409
-0.0022281672331383034
-0.0007411803226937619
-0.0007411803226937619
-0.0007411803226937619
-0.0022281672331383034
-0.0037173685668816657
-0.0007411803226937619
-0.0022281672331383034
-0.0022281672331383034
-0.0007411803226937619
-0.0007411803226937619
-0.00520879092920737
-0.035514094500380844
-0.0007411803226937619
-0.00520879092920737
-0.0007411803226937619
-0.02024664567958021
-0.006702440954996565
-0.011196823809655296
-0.0022281672331383034
-0.00969645068554409
-0.0007411803226937619
-0.0007411803226937619
-0.0007411803226937619
-0.0007411803226937619
-0.0007411803226937619
-0.02480245529695128
-0.00969645068554409
-0.006702440954996565
-0.01571149737006774
-0.0037173685668816657
-0.0007411803226937619
-0.00222816723

-0.005656349204223256
-0.0065829184327633765
-0.0017279799532133196
-0.006119526502180301
-0.000575508038740357
-0.0038057823681145824
-0.005887911036550851
-0.005656349204223256
-0.004036916026572435
-0.006351195625961857
-0.0003451729531509884
-0.002650914738862028
-0.005656349204223256
-0.005887911036550851
-0.0012668317922046551
-0.006351195625961857
-0.005887911036550851
-0.004961985258806911
-0.005656349204223256
-0.0054248409803644175
-0.0054248409803644175
-0.005887911036550851
-0.005887911036550851
-0.0017279799532133196
-0.006119526502180301
-0.006119526502180301
-0.0051933863401585866
-0.00011489090959606616
-0.005887911036550851
-0.004961985258806911
-0.005887911036550851
-0.006119526502180301
-0.0028817815918171044
-0.005656349204223256
-0.0010363374338012697
-0.004961985258806911
-0.005887911036550851
-0.0054248409803644175
-0.004036916026572435
-0.0051933863401585866
-0.005887911036550851
-0.004268103120149363
-0.005887911036550851
-0.004961985258806911
-0.00565634920422

ZeroDivisionError: division by zero

In [ ]:
plot_precision_recall(X_train, y_train, X_test, y_test, BoW)

### Задание 3 (2 балла)
Теперь добавим в BoW стемминг. Для этого нам понадобится класс SnowballStemmer из пакета `nltk`

#### Методы
`__init__(X, voc_limit)` - инициализирует BoW, составляя словарь, который будет использоваться для векторизации предложений. Размер словаря должен быть не больше `voc_limit`, в него должны входить самые часто встречающиеся в выборке слова.

`transform(X)` - векторизует сообщения из набора.

In [ ]:
class BowStem:
    def __init__(self, X, voc_limit=1000):
        pass
        
    def transform(self, X):
        pass

In [ ]:
bows = BowStem(X_train, voc_limit=500)
X_train_bows = bows.transform(X_train)
X_test_bows = bows.transform(X_test)

In [ ]:
predictor = NaiveBayes(0.001)
predictor.fit(X_train_bows, y_train)
get_precision_recall_accuracy(predictor.predict(X_test_bows), y_test)

In [ ]:
plot_precision_recall(X_train, y_train, X_test, y_test, BowStem)